##  The Battle of Neighborhoods

### Code Notebook

Before getting the data and exploring it, first dependencies must be downloaded.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.8.3
  latest version: 4.8.4

Please update conda by running

    $ conda update -n base -c defaults conda



# All requested packages already installed.

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.8.3
  latest version: 4.8.4

Please update conda by running

    $ conda update -n base -c defaults conda



# All requested packages already installed.

Libraries imported.


Get dataset of New York City's boroughs, the neighborhoods within them, and the latitude-longitude coordinates of each neighborhood.

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


Load the data.

In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

A quick look at the data:

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

All of the relevant data is in the *features* key, which is basically a list of the neighborhoods. A new variable is defined that includes this data below:

In [5]:
neighborhoods_data = newyork_data['features']

The first item in this list:

In [6]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Transform the data into a *pandas* dataframe:

The next task is essentially transforming this data of nested Python dictionaries into a *pandas* dataframe, which starts with the creation of an empty dataframe.

In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

A quick look at the empty dataframe confirms that the columns are as intended.

In [8]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Loop through the data and fill the dataframe one row at a time:

In [9]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

A quick look at the resulting dataframe:

In [10]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

And a quick check to make sure that the dataset has all 5 boroughs and 306 neighborhoods:

In [11]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.

In order to define an instance of the geocoder, a user_agent must be defined. The agent will be named <em>ny_explorer</em>, as shown below.

In [12]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.

In [13]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

Next, the utilization of the Foursquare API to explore the neighborhoods.

#### Define Foursquare Credentials and Version

In [14]:
CLIENT_ID = 'OGNVXAD3GBDK5JU2MPCPLI5FAEGNDD4Q2AOGW0IPU12XHP3E' # your Foursquare ID
CLIENT_SECRET = 'JX4GYQCL54D1CG40E4YRAR3WXS51RWO3G3LF1JAWQOQF0EHK' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: OGNVXAD3GBDK5JU2MPCPLI5FAEGNDD4Q2AOGW0IPU12XHP3E
CLIENT_SECRET:JX4GYQCL54D1CG40E4YRAR3WXS51RWO3G3LF1JAWQOQF0EHK


#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [15]:
neighborhoods.loc[0, 'Neighborhood']

'Wakefield'

Get the neighborhood's latitude and longitude values.

In [16]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.89470517661, -73.84720052054902.


#### Get the top 100 venues that are in Wakefield within a radius of 500 meters.

First, create the GET request URL, named **url**.

In [17]:
# type your answer here

LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 500 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL



'https://api.foursquare.com/v2/venues/explore?&client_id=OGNVXAD3GBDK5JU2MPCPLI5FAEGNDD4Q2AOGW0IPU12XHP3E&client_secret=JX4GYQCL54D1CG40E4YRAR3WXS51RWO3G3LF1JAWQOQF0EHK&v=20180605&ll=40.89470517661,-73.84720052054902&radius=500&limit=100'

Send the GET request and examine the resutls

In [18]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f36fbe156e24d60839f177c'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Wakefield',
  'headerFullLocation': 'Wakefield, Bronx',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 10,
  'suggestedBounds': {'ne': {'lat': 40.899205181110005,
    'lng': -73.84125857127495},
   'sw': {'lat': 40.89020517211, 'lng': -73.8531424698231}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c537892fd2ea593cb077a28',
       'name': 'Lollipops Gelato',
       'location': {'address': '4120 Baychester Ave',
        'crossStreet': 'Edenwald & Bussing Ave',
        'lat': 40.894123150205274,
        'lng': -73.84589162362325,
        'labeledLatL

All the information is in the *items* key. Borrow the **get_category_type** function from the Foursquare lab.

In [19]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Clean the json and structure it into a *pandas* dataframe.

In [20]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name      categories        lat        lng
0  Lollipops Gelato    Dessert Shop  40.894123 -73.845892
1          Rite Aid        Pharmacy  40.896649 -73.844846
2         Walgreens        Pharmacy  40.896528 -73.844700
3  Carvel Ice Cream  Ice Cream Shop  40.890487 -73.848568
4             Shell     Gas Station  40.894187 -73.845862

How many venues were returned by Foursquare?

In [21]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

10 venues were returned by Foursquare.


## Explore Neighborhoods in Manhattan

#### Utilize a function to repeat the same process to all the neighborhoods in Manhattan

In [22]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Run the above function on each neighborhood and create a new dataframe called *nyc_venues*.

In [25]:
nyc_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

#### Check the size of the resulting dataframe

In [26]:
print(nyc_venues.shape)
nyc_venues.head()

(10033, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2         Walgreens       40.896528       -73.844700        Pharmacy  
3  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
4             Shell       40.894187       -73.845862     Gas Station

Check how many venues were returned for each neighborhood

In [27]:
nyc_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      29                      29   
Annadale                                      10                      10   
Arden Heights                                  5                       5   
Arlington                                      8                       8   
Arrochar                                      21                      21   
Arverne                                       19                      19   
Astoria                                      100                     100   
Astoria Heights                               14                      14   
Auburndale                                    20                      20   
Bath Beach                                    47                      47   
Battery Park City                             73                      73   
Bay Ridge                                     83                      83   
Bay Terrace                                   48                      48   
Baychester                                    20                      20   
Bayside                                       73                      73   
Bayswater                                      1                       1   
Bedford Park                                  33                      33   
Bedford Stuyvesant                            28                      28   
Beechhurst                                    13                      13   
Bellaire                                      11                      11   
Belle Harbor                                  17                      17   
Bellerose                                     20                      20   
Belmont                                       98                      98   
Bensonhurst                                   40                      40   
Bergen Beach                                   5                       5   
Blissville                                    17                      17   
Bloomfield                                     4                       4   
Boerum Hill                                   89                      89   
Borough Park                                  21                      21   
Breezy Point                                   5                       5   
Briarwood                                     11                      11   
Brighton Beach                                44                      44   
Broad Channel                                  6                       6   
Broadway Junction                             16                      16   
Bronxdale                                     12                      12   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   19                      19   
Bulls Head                                    41                      41   
Bushwick                                      69                      69   
Butler Manor                                   7                       7   
Cambria Heights                               11                      11   
Canarsie                                       6                       6   
Carnegie Hill                                 86                      86   
Carroll Gardens                              100                     100   
Castle Hill                                    7                       7   
Castleton Corners                             16                      16   
Central Harlem                                44                      44   
Charleston                                    30                      30   
Chelsea                                      106                     106   
Chinatown                                    100                     100   

#### Check how many unique categories can be curated from all the returned venues

In [28]:
print('There are {} uniques categories.'.format(len(nyc_venues['Venue Category'].unique())))

There are 421 uniques categories.


## Analyze Each Neighborhood

In [29]:
# one hot encoding
nyc_onehot = pd.get_dummies(nyc_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
nyc_onehot['Neighborhood'] = nyc_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [nyc_onehot.columns[-1]] + list(nyc_onehot.columns[:-1])
nyc_onehot = nyc_onehot[fixed_columns]

nyc_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                0          0           0           0       0     0    0   
1                0          0           0           0       0     0    0   
2                0          0           0           0       0     0    0   
3                0          0           0           0       0     0    0   
4                0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Bath House  Beach  \
0               0                 0                 0           0      0   
1               0                 0                 0           0      0   
2               0                 0                 0           0      0   
3               0                 0                 0           0      0   
4               0                 0                 0           0      0   

   Beach Bar  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0          0         0            0           0              0   
1          0         0            0           0              0   
2          0         0            0           0              0   
3          0         0            0           0              0   
4          0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0     

Examine the new dataframe size.

In [49]:
nyc_onehot.shape

(10033, 421)

#### Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [50]:
nyc_grouped = nyc_onehot.groupby('Neighborhood').mean().reset_index()
nyc_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.012048           0.000000   
12                 Bay Terrace     0.000000           0.020833   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.013699           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.076923           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.022472           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.040000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.034884           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.010000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.032258           0.000000   
59                  Co-op City     0.000000           0.00

#### Confirm the new size

In [51]:
nyc_grouped.shape

(301, 421)

#### Let's print each neighborhood along with the top 5 most common venues

In [52]:
num_top_venues = 5

for hood in nyc_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = nyc_grouped[nyc_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                   venue  freq
0            Pizza Place  0.17
1     Chinese Restaurant  0.07
2            Supermarket  0.07
3          Deli / Bodega  0.07
4  Check Cashing Service  0.03


----Annadale----
                 venue  freq
0          Pizza Place   0.2
1           Restaurant   0.1
2  American Restaurant   0.1
3        Train Station   0.1
4                  Bar   0.1


----Arden Heights----
           venue  freq
0  Deli / Bodega   0.2
1       Pharmacy   0.2
2    Coffee Shop   0.2
3       Bus Stop   0.2
4    Pizza Place   0.2


----Arlington----
                   venue  freq
0               Bus Stop  0.25
1            Coffee Shop  0.12
2  General Entertainment  0.12
3          Boat or Ferry  0.12
4    American Restaurant  0.12


----Arrochar----
                       venue  freq
0                   Bus Stop  0.14
1              Deli / Bodega  0.10
2         Italian Restaurant  0.10
3             Cosmetics Shop  0.05
4  Middle Eastern Restaurant  0.05


----A

#### Put that into a *pandas* dataframe

Utilize a function to sort the venues in descending order.

In [53]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Create the new dataframe and display the top 10 venues for each neighborhood.

In [54]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = nyc_grouped['Neighborhood']

for ind in np.arange(nyc_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(nyc_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place         Deli / Bodega   
1       Annadale           Pizza Place                   Bar   
2  Arden Heights         Deli / Bodega           Pizza Place   
3      Arlington              Bus Stop         Deli / Bodega   
4       Arrochar              Bus Stop         Deli / Bodega   

  3rd Most Common Venue     4th Most Common Venue  5th Most Common Venue  \
0           Supermarket        Chinese Restaurant       Department Store   
1              Pharmacy             Train Station                   Food   
2              Bus Stop               Coffee Shop               Pharmacy   
3           Coffee Shop       American Restaurant  General Entertainment   
4    Italian Restaurant  Mediterranean Restaurant                  Hotel   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0         Grocery Store  Check Cashing Service           Bus Station   
1   American Restaurant                  Diner            Restaurant   
2    Dim Sum Restaurant                  Diner               Factory   
3         Boat or Ferry          Grocery Store           Fish Market   
4        Sandwich Place  Outdoors & Recreation    Athletics & Sports   

  9th Most Common Venue 10th Most Common Venue  
0   Martial Arts School   Fast Food Restaurant  
1          Dance Studio                Factory  
2    Falafel Restaurant                   Farm  
3    Falafel Restaurant                   Farm  
4           Pizza Place            Supermarket

Create copy of dataframe to modify.

In [55]:
neighborhoods_venues_counted = neighborhoods_venues_sorted
neighborhoods_venues_counted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place         Deli / Bodega   
1       Annadale           Pizza Place                   Bar   
2  Arden Heights         Deli / Bodega           Pizza Place   
3      Arlington              Bus Stop         Deli / Bodega   
4       Arrochar              Bus Stop         Deli / Bodega   

  3rd Most Common Venue     4th Most Common Venue  5th Most Common Venue  \
0           Supermarket        Chinese Restaurant       Department Store   
1              Pharmacy             Train Station                   Food   
2              Bus Stop               Coffee Shop               Pharmacy   
3           Coffee Shop       American Restaurant  General Entertainment   
4    Italian Restaurant  Mediterranean Restaurant                  Hotel   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0         Grocery Store  Check Cashing Service           Bus Station   
1   American Restaurant                  Diner            Restaurant   
2    Dim Sum Restaurant                  Diner               Factory   
3         Boat or Ferry          Grocery Store           Fish Market   
4        Sandwich Place  Outdoors & Recreation    Athletics & Sports   

  9th Most Common Venue 10th Most Common Venue  
0   Martial Arts School   Fast Food Restaurant  
1          Dance Studio                Factory  
2    Falafel Restaurant                   Farm  
3    Falafel Restaurant                   Farm  
4           Pizza Place            Supermarket

Create new column to count how many "Most Common" spots are occupied by food serving venues.

In [56]:
neighborhoods_venues_counted.insert(11, "# of Most Common Venue Positions Taken by Food-Serving Places", 0)

In [57]:
neighborhoods_venues_counted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place         Deli / Bodega   
1       Annadale           Pizza Place                   Bar   
2  Arden Heights         Deli / Bodega           Pizza Place   
3      Arlington              Bus Stop         Deli / Bodega   
4       Arrochar              Bus Stop         Deli / Bodega   

  3rd Most Common Venue     4th Most Common Venue  5th Most Common Venue  \
0           Supermarket        Chinese Restaurant       Department Store   
1              Pharmacy             Train Station                   Food   
2              Bus Stop               Coffee Shop               Pharmacy   
3           Coffee Shop       American Restaurant  General Entertainment   
4    Italian Restaurant  Mediterranean Restaurant                  Hotel   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0         Grocery Store  Check Cashing Service           Bus Station   
1   American Restaurant                  Diner            Restaurant   
2    Dim Sum Restaurant                  Diner               Factory   
3         Boat or Ferry          Grocery Store           Fish Market   
4        Sandwich Place  Outdoors & Recreation    Athletics & Sports   

  9th Most Common Venue 10th Most Common Venue  \
0   Martial Arts School   Fast Food Restaurant   
1          Dance Studio                Factory   
2    Falafel Restaurant                   Farm   
3    Falafel Restaurant                   Farm   
4           Pizza Place            Supermarket   

   # of Most Common Venue Positions Taken by Food-Serving Places  
0                                                  0              
1                                                  0              
2                                                  0              
3                                                  0              
4                                                  0

Establish which venues will be classified as "food-serving".

In [58]:
food_list = ['Pizza Place',
             'Breakfast Spot',
             'Diner',
             'Food', #real specific, that.
             'Coffee Shop', 
             'Sandwich Place', 
             'Noodle House', 
             'Donut Shop',
             'Burger Joint', 
             'Fried Chicken Joint',
             'Pub', #some have a food menu
             'Bar', #ditto
             'Ice Cream Shop',
             'Food Truck',
             'Bakery',
             'Bagel Shop',
             'Café',
             'Gourmet Shop',
             'Dessert Shop',
             'Food Court',
             'Salad Place',
             'Irish Pub',
             'BBQ Joint',
             'Bistro',
             'Buffet',
             'Burrito Place',
             'Cafeteria',
             'Creperie',
             'Cupcake Shop',
             'Fish & Chips Shop',
             'Food & Drink Shop',
            'Food Stand',
            'Frozen Yogurt Shop',
            'Gaming Cafe',
            'Gastropub',
            'Hot Dog Joint',
            'Pie Shop',
            'Sports Bar',
            'Steakhouse',
            'Taco Place']



In [59]:
def evaluate_food_option(item):
    
    is_true = False
    
    if((item in food_list) or ('Restaurant' in item)): #Anything in the above list or containing the word "Restaurant"
        is_true = True
       
    return is_true

Modify table to count how many "Most Common" spots are taken by a venue listed above.

In [60]:
for ind in np.arange(neighborhoods_venues_counted.shape[0]):
    venues = 0
    
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 1]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 2]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 3]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 4]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 5]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 6]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 7]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 8]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 9]) == True):
        venues += 1
    if(evaluate_food_option(neighborhoods_venues_counted.iloc[ind, 10]) == True):
        venues += 1
    
    neighborhoods_venues_counted.at[ind, '# of Most Common Venue Positions Taken by Food-Serving Places'] = venues
    
neighborhoods_venues_counted

Neighborhood       1st Most Common Venue  \
0                     Allerton                 Pizza Place   
1                     Annadale                 Pizza Place   
2                Arden Heights               Deli / Bodega   
3                    Arlington                    Bus Stop   
4                     Arrochar                    Bus Stop   
5                      Arverne                   Surf Spot   
6                      Astoria                         Bar   
7              Astoria Heights               Deli / Bodega   
8                   Auburndale          Italian Restaurant   
9                   Bath Beach          Chinese Restaurant   
10           Battery Park City                        Park   
11                   Bay Ridge                 Pizza Place   
12                 Bay Terrace              Clothing Store   
13                  Baychester                  Donut Shop   
14                     Bayside                         Bar   
15                   Bayswater                  Playground   
16                Bedford Park                       Diner   
17          Bedford Stuyvesant               Deli / Bodega   
18                  Beechhurst                 Yoga Studio   
19                    Bellaire            Greek Restaurant   
20                Belle Harbor                       Beach   
21                   Bellerose                 Pizza Place   
22                     Belmont          Italian Restaurant   
23                 Bensonhurst          Chinese Restaurant   
24                Bergen Beach             Harbor / Marina   
25                  Blissville                  Donut Shop   
26                  Bloomfield           Recreation Center   
27                 Boerum Hill                Dance Studio   
28                Borough Park                        Bank   
29                Breezy Point                       Beach   
30                   Briarwood               Deli / Bodega   
31              Brighton Beach          Russian Restaurant   
32               Broad Channel                 Pizza Place   
33           Broadway Junction               Deli / Bodega   
34                   Bronxdale          Italian Restaurant   
35            Brooklyn Heights                 Yoga Studio   
36                  Brookville               Deli / Bodega   
37                 Brownsville               Moving Target   
38                  Bulls Head                    Bus Stop   
39                    Bushwick                         Bar   
40                Butler Manor              Baseball Field   
41             Cambria Heights        Caribbean Restaurant   
42                    Canarsie               Deli / Bodega   
43               Carnegie Hill                 Coffee Shop   
44             Carroll Gardens          Italian Restaurant   
45                 Castle Hill                    Pharmacy   
46           Castleton Corners                 Pizza Place   
47              Central Harlem          African Restaurant   
48                  Charleston                 Coffee Shop   
49                     Chelsea                 Coffee Shop   
50                   Chinatown          Chinese Restaurant   
51                 City Island      Thrift / Vintage Store   
52                   City Line                  Donut Shop   
53                Civic Center                 Coffee Shop   
54           Claremont Village               Grocery Store   
55                Clason Point                        Park   
56                     Clifton               Grocery Store   
57                     Clinton        Gym / Fitness Center   
58                Clinton Hill          Italian Restaurant   
59                  Co-op City                 Bus Station   
60                 Cobble Hill                 Pizza Place   
61               College Point               Deli / Bodega   
62                     Concord      Thrift / Vintage Store   
63                   Concourse               Groce

The best place to open a restaurant would be a place where food-serving establishments are not common. Therefore, if 0 "Most Common" places were taken by food-serving establishments, that would be the perfect neighborhood to open in.

In [62]:
neighborhoods_venues_counted.loc[neighborhoods_venues_counted['# of Most Common Venue Positions Taken by Food-Serving Places'] == 0]

Empty DataFrame
Columns: [Neighborhood, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, # of Most Common Venue Positions Taken by Food-Serving Places]
Index: []

However, no such neighborhood exists. The next best thing is a neighborhood where only one "Most Common" spot is taken.

In [63]:
neighborhoods_venues_counted.loc[neighborhoods_venues_counted['# of Most Common Venue Positions Taken by Food-Serving Places'] == 1]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
24   Bergen Beach       Harbor / Marina        Baseball Field   
29   Breezy Point                 Beach   Monument / Landmark   
55   Clason Point                  Park              Bus Stop   
94      Fieldston                 Plaza                 River   
222  Queensbridge        Sandwich Place                 Hotel   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
24     Athletics & Sports            Playground         Women's Store   
29            Supermarket                 Trail         Women's Store   
55      Convenience Store         Grocery Store                  Pool   
94            Music Venue           Bus Station         Women's Store   
222    Athletics & Sports             Hotel Bar  Gym / Fitness Center   

    6th Most Common Venue      7th Most Common Venue 8th Most Common Venue  \
24                Exhibit                 Eye Doctor               Factory   
29             Eye Doctor                    Factory    Falafel Restaurant   
55          Boat or Ferry  South American Restaurant         Women's Store   
94             Eye Doctor                    Factory    Falafel Restaurant   
222      Basketball Court             Baseball Field                  Park   

          9th Most Common Venue 10th Most Common Venue  \
24           Falafel Restaurant                   Farm   
29                         Farm         Farmers Market   
55   Financial or Legal Service                Factory   
94                         Farm         Farmers Market   
222              Scenic Lookout            Beer Garden   

     # of Most Common Venue Positions Taken by Food-Serving Places  
24                                                   1              
29                                                   1              
55                                                   1              
94                                                   1              
222                                                  1

According to this data, the best neighborhood to open a restaurant is Bergen Beach, Breezy Point, Clason Point, Fieldston, or Queensbridge.

In [64]:
neighborhoods_venues_counted.loc[neighborhoods_venues_counted['# of Most Common Venue Positions Taken by Food-Serving Places'] == 10]

Empty DataFrame
Columns: [Neighborhood, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue, # of Most Common Venue Positions Taken by Food-Serving Places]
Index: []

In [65]:
neighborhoods_venues_counted.loc[neighborhoods_venues_counted['# of Most Common Venue Positions Taken by Food-Serving Places'] == 9]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
14           Bayside                   Bar      Sushi Restaurant   
206       Park Slope           Coffee Shop          Burger Joint   
245   Sheepshead Bay    Turkish Restaurant          Dessert Shop   
278  Upper West Side    Italian Restaurant           Coffee Shop   
299         Woodside         Grocery Store                Bakery   

         3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
14           Indian Restaurant   American Restaurant           Pizza Place   
206                Pizza Place            Bagel Shop    Chinese Restaurant   
245             Sandwich Place           Yoga Studio    Italian Restaurant   
278   Mediterranean Restaurant                Bakery                   Bar   
299  Latin American Restaurant   Filipino Restaurant       Thai Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
14     Mexican Restaurant            Steakhouse          Burger Joint   
206    Mexican Restaurant                   Pub                Bakery   
245              Creperie                 Diner            Restaurant   
278     Indian Restaurant              Wine Bar           Pizza Place   
299                   Bar            Donut Shop   American Restaurant   

    9th Most Common Venue 10th Most Common Venue  \
14                    Spa                 Bakery   
206             Pet Store    American Restaurant   
245    Russian Restaurant            Pizza Place   
278          Dessert Shop             Sports Bar   
299                   Pub                   Café   

     # of Most Common Venue Positions Taken by Food-Serving Places  
14                                                   9              
206                                                  9              
245                                                  9              
278                                                  9              
299                                                  9

In comparison, the worst neighborhood to open a restaurant is Bayside, Park Slope, Sheepshead Bay, Upper West Side, or Woodside.